In [1]:
import json
import torch
import random
from PIL import Image
from tqdm import tqdm
import pickle
import re
import subprocess


In [2]:
#dir = "/home/dhruv/Projects/imSitu_Clip/imSitu/"
#dir = '/home/roy/usrdata/imSitu/imSitu_annotations/'

train = json.load(open('/home/dhruv/Projects/VidSitu/vidsitu_data/vidsitu_annotations/vseg_ann_files/vsann_train_lb.json', 'r'))

valid_random_GT = json.load(open('/home/dhruv/Projects/VidSitu/vidsitu_data/vidsitu_annotations/vidsitu_valid_subset_GT.json', 'r'))

#train = json.load(open("../imSitu/train.json"))
#val = json.load(open(dir + "dev.json"))
#test = json.load(open(dir + "test.json"))
# imsitu_space = json.load(open(dir + "imsitu_space.json"))
# nouns = imsitu_space["nouns"]
# verbs = imsitu_space["verbs"]

In [4]:
with open('/home/dhruv/Projects/VidSitu/vidsitu_data/vidsitu_annotations/split_files/vseg_split_valid_lb.json', 'r') as f:
    val_split = json.load(f)

In [4]:
import os.path as osp
import cv2
def check_video_length(video_path, expected_duration=10):
    if not osp.exists(video_path):
        return False, "Video file does not exist."

    cap = cv2.VideoCapture(video_path)
    if not cap.isOpened():
        return False, "Unable to load video file."

    fps = cap.get(cv2.CAP_PROP_FPS)
    frame_count = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
    duration = frame_count / fps
    cap.release()

    if duration < expected_duration:
        return False, f"Video duration is less than expected: {duration} seconds."
    return True, ""

In [12]:
check_video_length('../../VidSitu/vidsitu_data/vsitu_video_trimmed_dir/v_VYQoxBs5N2A_seg_90_100.mp4')

(True, '')

In [11]:
vid

'../VidSitu/vidsitu_data/vsitu_video_trimmed_dir/v_VYQoxBs5N2A_seg_90_100.mp4'

In [10]:
osp.exists(vid)

False

In [ ]:
v_VYQoxBs5N2A_seg_120_130

In [14]:
#vid = '../VidSitu/vidsitu_data/vsitu_video_trimmed_dir/v_S-2cloMm4Lk_seg_95_105.mp4'
vid = '../../VidSitu/vidsitu_data/vsitu_video_trimmed_dir/v_VYQoxBs5N2A_seg_120_130.mp4'
from IPython.display import Video

Video(vid, embed=True)

In [5]:
valid_random_GT

[{'Ev1': {'vid_uid': 'VYQoxBs5N2A1',
   'vid_seg_int': 'v_VYQoxBs5N2A_seg_120_130',
   'EvRel': 'Enables',
   'Args': {'Arg0 (driver)': 'man in a black police uniform',
    'Arg1 (vehicle or path)': 'car',
    'ArgM (direction)': 'forward',
    'ArgM (manner)': 'casually',
    'Scene of the Event': 'down a street'},
   'Arg_List': {'Arg0 (driver)': '0',
    'Arg1 (vehicle or path)': '1',
    'ArgM (direction)': '2',
    'ArgM (manner)': '3',
    'Scene of the Event': '4'},
   'Verb': 'drive (drive a vehicle)',
   'VerbID': 'drive.01'},
  'Ev2': {'vid_uid': 'VYQoxBs5N2A1',
   'vid_seg_int': 'v_VYQoxBs5N2A_seg_120_130',
   'EvRel': 'Enables',
   'Args': {'Arg0 (driver)': 'man in a black police uniform',
    'Arg1 (vehicle or path)': 'car',
    'ArgM (direction)': 'forward',
    'ArgM (manner)': 'casually',
    'Scene of the Event': 'down a street'},
   'Arg_List': {'Arg0 (driver)': '0',
    'Arg1 (vehicle or path)': '1',
    'ArgM (direction)': '2',
    'ArgM (manner)': '3',
    'Scene o

In [8]:
len(val_split)

1326

In [1]:
for clip_info in valid_random_GT[:1]:
    clip_name = clip_info["Ev1"]["vid_seg_int"]
    
    clip_results = {}
    for event_index, event_key in enumerate(["Ev1"]):
        event_info = clip_info[event_key]
        event_results = []


NameError: name 'valid_random_GT' is not defined

In [8]:

# Define the model path
MODEL = "../ckpts/ckpts_v3.5/linear_40960/vidsitu_sft_imgx16_VILA1.5_3B_40960_linear_Bank0_LearnLat0"

## Evaluate in notebook

Refer to /vila_llama3/imsituSFT_inference.sh to run script.

In [6]:
# Directory containing the images
#image_dir = "./of500_images_resized/"
video_dir = '../VidSitu/vidsitu_data/vsitu_video_trimmed_dir/'
# Function to run the command for a single image and return the output
def run_command(video):
    command = [
        "python", "-W", "ignore", "../llava/eval/run_vila.py",
        "--model-path", MODEL,
        "--conv-mode", "v1",
        "--max_new_tokens", "1024",
        "--query", "<image>\n Task ImSitu: Generate the verb and corresponding roles, then generate the noun based on the verb and roles",
        "--video-file", f"{video_dir}{video}"
    ]
    
    result = subprocess.run(command, capture_output=True, text=True)
    # Extract the JSON part using regex
    json_match = re.search(r'\{.*\}', result.stdout)
    if json_match:
        return json.loads(json_match.group(0))
    else:
        return None
    #return result.stdout, result.stderr

In [7]:
# Dictionary to store the results
results = {}

# Loop over the development set images and run the command for each
for image in tqdm(dev_images):
    #print(f"Processing {image}...")
    output = run_command(image)
    #print(output)
    if output:
        results[image] = output
    else:
        print(f"Failed to extract JSON for image {image}")

# Save the results to a JSON file
with open("vidsitu_SFToutput_val.json", "w") as outfile:
    json.dump(results, outfile)

print("Processing complete. Results saved to imsitu_dev_SFT_results.json.")

  0%|          | 0/25200 [00:00<?, ?it/s]


NameError: name 'MODEL' is not defined

In [ ]:
from pycocoevalcap.cider.cider import Cider
import evaluate
import numpy as np
metrics = {}
for name in ['rouge', 'meteor']: #bleu
    metrics[name] = evaluate.load(name)
metrics['cider'] = Cider()


In [ ]:
from collections import defaultdict

def compute_metrics(decoded_labels, decoded_predictions):
    print("first 5 GT: ", decoded_labels[:5])
    print("first 5 Pred: ", decoded_predictions[:5])
    
    result = defaultdict(dict)
    for key, metric in metrics.items():
        if key in ['rouge', 'bleu', 'meteor']:
            # Compute the metric directly for these cases
            result[key] = metric.compute(predictions=decoded_predictions, references=decoded_labels)
        elif key in ['cider']:
            # Create dictionaries for GT and predictions as required by the CIDEr metric
            gt_dict = {cs: [decoded_labels[cs]] for cs in range(len(decoded_labels))}
            pred_dict = {cs: [decoded_predictions[cs]] for cs in range(len(decoded_predictions))}
            # Compute the CIDEr score
            cider_score = metric.compute_score(gt_dict, pred_dict)
            result[key] = cider_score[0]
    
    return dict(result)

In [ ]:
json_match = re.search(r'\{.*\}', results['hitchhiking_238.jpg'])
if json_match:
    print(json.loads(json_match.group(0)))

TypeError: expected string or bytes-like object

In [ ]:
results['hitchhiking_238.jpg'][0]

'[2024-06-27 15:55:49,727] [INFO] [real_accelerator.py:203:get_accelerator] Setting ds_accelerator to cuda (auto detect)\n\x1b [WARNING] \x1b async_io requires the dev libaio .so object and headers but these were not found.\n\x1b [WARNING] \x1b async_io: please install the libaio-dev package with apt\n\x1b [WARNING] \x1b If libaio is already installed (perhaps from source), try setting the CFLAGS and LDFLAGS environment variables to where it can be found.\n\x1b [WARNING] \x1b Please specify the CUTLASS repo directory as environment variable $CUTLASS_PATH\n\x1b [WARNING] \x1b sparse_attn requires a torch version >= 1.5 and < 2.0 but detected 2.3\n\x1b [WARNING] \x1b using untested triton version (2.3.0), only 1.0.0 is known to be compatible\nPlain Model use_bank 0\nPlain Model learnable_latent =1\n[WARNING] Insert Bank 0 with Learnable Latent 1\ninput:  <image>\n Task ImSitu: Generate the verb and corresponding roles, then generate the noun based on the verb and roles\n[WARNING] the aut

In [ ]:
dev_images[3]

'grieving_75.jpg'

In [3]:


vid = '../VidSitu/vidsitu_data/vsitu_video_trimmed_dir/v_VYQoxBs5N2A_seg_120_130.mp4'
# open vid
from IPython.display import Video

Video(vid,embed=True)

In [ ]:
image

'hitchhiking_238.jpg'

In [ ]:
output, error = run_command(image)

In [ ]:
output

'[2024-06-27 15:48:50,766] [INFO] [real_accelerator.py:203:get_accelerator] Setting ds_accelerator to cuda (auto detect)\n\x1b [WARNING] \x1b async_io requires the dev libaio .so object and headers but these were not found.\n\x1b [WARNING] \x1b async_io: please install the libaio-dev package with apt\n\x1b [WARNING] \x1b If libaio is already installed (perhaps from source), try setting the CFLAGS and LDFLAGS environment variables to where it can be found.\n\x1b [WARNING] \x1b Please specify the CUTLASS repo directory as environment variable $CUTLASS_PATH\n\x1b [WARNING] \x1b sparse_attn requires a torch version >= 1.5 and < 2.0 but detected 2.3\n\x1b [WARNING] \x1b using untested triton version (2.3.0), only 1.0.0 is known to be compatible\nPlain Model use_bank 0\nPlain Model learnable_latent =1\n[WARNING] Insert Bank 0 with Learnable Latent 1\ninput:  <image>\n Task ImSitu: Generate the verb and corresponding roles, then generate the noun based on the verb and roles\n[WARNING] the aut

In [ ]:
json_match = re.search(r'\{.*\}', output)
if json_match:
    parsed_output = json.loads(json_match.group(0))

In [ ]:
parsed_output

{'verb': 'hitchhiking',
 'roles': {'1': 'place', '2': 'agent'},
 'nouns': {'place': 'highway', 'agent': 'man'}}

## Evaluate Scores

In [2]:
from pycocoevalcap.cider.cider import Cider
import evaluate
import numpy as np
metrics = {}
for name in ['rouge', 'meteor']: #bleu
    metrics[name] = evaluate.load(name)
metrics['cider'] = Cider()

/home/dhruv/anaconda3/envs/vila2/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/home/dhruv/anaconda3/envs/vila2/lib/python3.10/site-packages/transformers/utils/generic.py:441: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(


[2024-07-15 20:24:57,740] [INFO] [real_accelerator.py:203:get_accelerator] Setting ds_accelerator to cuda (auto detect)
 [WARNING]  async_io requires the dev libaio .so object and headers but these were not found.
 [WARNING]  async_io: please install the libaio-dev package with apt
 [WARNING]  If libaio is already installed (perhaps from source), try setting the CFLAGS and LDFLAGS environment variables to where it can be found.
 [WARNING]  Please specify the CUTLASS repo directory as environment variable $CUTLASS_PATH


/home/dhruv/anaconda3/envs/vila2/compiler_compat/ld: cannot find -laio: No such file or directory
collect2: error: ld returned 1 exit status


 [WARNING]  sparse_attn requires a torch version >= 1.5 and < 2.0 but detected 2.3
 [WARNING]  using untested triton version (2.3.0), only 1.0.0 is known to be compatible


/home/dhruv/anaconda3/envs/vila2/lib/python3.10/site-packages/transformers/utils/generic.py:309: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(
/home/dhruv/anaconda3/envs/vila2/lib/python3.10/site-packages/transformers/utils/generic.py:309: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(
[nltk_data] Downloading package wordnet to /home/dhruv/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [3]:
from collections import defaultdict

def compute_metrics(decoded_labels, decoded_predictions):
    print("first 5 GT: ", decoded_labels[:5])
    print("first 5 Pred: ", decoded_predictions[:5])
    
    result = defaultdict(dict)
    for key, metric in metrics.items():
        if key in ['rouge', 'bleu', 'meteor']:
            # Compute the metric directly for these cases
            result[key] = metric.compute(predictions=decoded_predictions, references=decoded_labels)
        elif key in ['cider']:
            # Create dictionaries for GT and predictions as required by the CIDEr metric
            gt_dict = {cs: [decoded_labels[cs]] for cs in range(len(decoded_labels))}
            pred_dict = {cs: [decoded_predictions[cs]] for cs in range(len(decoded_predictions))}
            # Compute the CIDEr score
            cider_score = metric.compute_score(gt_dict, pred_dict)
            result[key] = cider_score[0]
    
    return dict(result)

In [19]:
import re
from collections import defaultdict
import evaluate
from pycocoevalcap.cider.cider import Cider

def normalize_role_name(role_name):
    """
    Normalize the 'Arg #' part of the role name by removing spaces.
    """
    return re.sub(r'Arg\s*(\d+)', r'Arg\1', role_name)

def evaluate_predictions(output, GT, return_dict=False):
    predictions = []
    ground_truths = []
    index = []

    for vid_seg, events in output.items():
        for event_key, event_data in events.items():
            event_gt = None
            for gt_event in GT:
                if gt_event[event_key]["vid_seg_int"] == vid_seg:
                    event_gt = gt_event[event_key]
                    break

            if not event_gt:
                print(f"No GT found for {vid_seg} {event_key}")
                continue

            gt_args = {normalize_role_name(role): gt_noun for role, gt_noun in event_gt["Args"].items()}

            for role, predicted_noun in event_data["nouns"].items():
                role = normalize_role_name(role)
                if role not in gt_args:
                    continue

                #predicted_noun = event_data["nouns"].get(role, "")
                if predicted_noun == []:
                    predicted_noun = [""]

                index.append(f"{vid_seg}-{event_key}-{role}")
                predictions.append(predicted_noun)  # Assuming there's only one prediction per role
                ground_truths.append(gt_args[role])  # Add corresponding GT value or empty if role not in GT

    if return_dict:
        return {'index': index, 'predictions': predictions, 'ground_truths': ground_truths}
    
    results = compute_metrics(ground_truths, predictions)
    return results

def compute_metrics(decoded_labels, decoded_predictions):
    print("First 5 GT: ", decoded_labels[:5])
    print("First 5 Pred: ", decoded_predictions[:5])
    
    result = defaultdict(dict)
    for key, metric in metrics.items():
        if key in ['rouge', 'meteor']:
            # Compute the metric directly for these cases
            result[key] = metric.compute(predictions=decoded_predictions, references=decoded_labels)
        elif key in ['cider']:
            # Create dictionaries for GT and predictions as required by the CIDEr metric
            gt_dict = {cs: [decoded_labels[cs]] for cs in range(len(decoded_labels))}
            pred_dict = {cs: [decoded_predictions[cs]] for cs in range(len(decoded_predictions))}
            # Compute the CIDEr score
            cider_score = metric.compute_score(gt_dict, pred_dict)
            result[key] = cider_score[0]
    
    return dict(result)

# Initialize metrics
metrics = {}
for name in ['rouge', 'meteor']:  # Add 'bleu' if needed
    metrics[name] = evaluate.load(name)
metrics['cider'] = Cider()

[nltk_data] Downloading package wordnet to /home/dhruv/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


### Add Verb Pred Eval

In [1]:
import re
from collections import defaultdict
import evaluate
from pycocoevalcap.cider.cider import Cider
import nltk

def normalize_role_name(role_name):
    """
    Normalize the 'Arg #' part of the role name by removing spaces.
    """
    return re.sub(r'Arg\s*(\d+)', r'Arg\1', role_name)

def evaluate_predictions(output, GT, return_dict=False):
    predictions = []
    ground_truths = []
    index = []

    verb_predictions = []
    verb_ground_truths = []

    for vid_seg, events in output.items():
        for event_key, event_data in events.items():
            event_gt = None
            for gt_event in GT:
                if gt_event[event_key]["vid_seg_int"] == vid_seg:
                    event_gt = gt_event[event_key]
                    break

            if not event_gt:
                print(f"No GT found for {vid_seg} {event_key}")
                continue

            gt_args = {normalize_role_name(role): gt_noun for role, gt_noun in event_gt["Args"].items()}

            # Evaluate verbs
            predicted_verb = event_data.get("verb", "")
            ground_truth_verb = event_gt["Verb"]

            verb_predictions.append(predicted_verb)
            verb_ground_truths.append(ground_truth_verb)

            # Evaluate roles and nouns
            for role_id, role in event_data["roles"].items():
                role = normalize_role_name(role)
                if role not in gt_args:
                    continue

                predicted_noun = event_data["nouns"].get(role, "")
                if predicted_noun == []:
                    predicted_noun = [""]

                index.append(f"{vid_seg}-{event_key}-{role}")
                predictions.append(predicted_noun)  # Assuming there's only one prediction per role
                ground_truths.append(gt_args[role])  # Add corresponding GT value or empty if role not in GT

    if return_dict:
        return {'index': index, 'predictions': predictions, 'ground_truths': ground_truths, 'verb_predictions': verb_predictions, 'verb_ground_truths': verb_ground_truths}

    noun_results = compute_metrics(ground_truths, predictions)
    verb_results = compute_metrics(verb_ground_truths, verb_predictions)

    results = {'nouns': noun_results, 'verbs': verb_results}
    return results

def compute_metrics(decoded_labels, decoded_predictions):
    print("First 5 GT: ", decoded_labels[:5])
    print("First 5 Pred: ", decoded_predictions[:5])
    
    result = defaultdict(dict)
    for key, metric in metrics.items():
        if key in ['rouge', 'meteor']:
            # Compute the metric directly for these cases
            result[key] = metric.compute(predictions=decoded_predictions, references=decoded_labels)
        elif key in ['cider']:
            # Create dictionaries for GT and predictions as required by the CIDEr metric
            gt_dict = {cs: [decoded_labels[cs]] for cs in range(len(decoded_labels))}
            pred_dict = {cs: [decoded_predictions[cs]] for cs in range(len(decoded_predictions))}
            # Compute the CIDEr score
            cider_score = metric.compute_score(gt_dict, pred_dict)
            result[key] = cider_score[0]
    
    return dict(result)

# Initialize metrics
metrics = {}
for name in ['rouge', 'meteor']:  # Add 'bleu' if needed
    metrics[name] = evaluate.load(name)
metrics['cider'] = Cider()

/home/dhruv/anaconda3/envs/vila2/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
/home/dhruv/anaconda3/envs/vila2/lib/python3.10/site-packages/transformers/utils/generic.py:441: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(


[2024-07-16 14:47:11,307] [INFO] [real_accelerator.py:203:get_accelerator] Setting ds_accelerator to cuda (auto detect)
 [WARNING]  async_io requires the dev libaio .so object and headers but these were not found.
 [WARNING]  async_io: please install the libaio-dev package with apt
 [WARNING]  If libaio is already installed (perhaps from source), try setting the CFLAGS and LDFLAGS environment variables to where it can be found.
 [WARNING]  Please specify the CUTLASS repo directory as environment variable $CUTLASS_PATH


/home/dhruv/anaconda3/envs/vila2/compiler_compat/ld: cannot find -laio: No such file or directory
collect2: error: ld returned 1 exit status


 [WARNING]  sparse_attn requires a torch version >= 1.5 and < 2.0 but detected 2.3
 [WARNING]  using untested triton version (2.3.0), only 1.0.0 is known to be compatible


/home/dhruv/anaconda3/envs/vila2/lib/python3.10/site-packages/transformers/utils/generic.py:309: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(
/home/dhruv/anaconda3/envs/vila2/lib/python3.10/site-packages/transformers/utils/generic.py:309: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(
[nltk_data] Downloading package wordnet to /home/dhruv/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [9]:
len(output)

1224

In [2]:
import json
valid_random_GT = json.load(open('/home/dhruv/Projects/VidSitu/vidsitu_data/vidsitu_annotations/vidsitu_valid_subset_GT.json', 'r'))
output = json.load(open('./vidsitu_SFToutput_val.json', 'r'))

In [13]:
len(output) * 5

6120

In [16]:
len(results['ground_truths']), len(results['predictions']), len(results['index']), len(results['verb_predictions']), len(results['verb_ground_truths'])

(9873, 9873, 9873, 6120, 6120)

In [14]:
len(results['index'])

9873

In [3]:
evaluate_predictions(output, valid_random_GT)

First 5 GT:  ['casually', 'casually', 'casually', 'intently', 'in a car']
First 5 Pred:  ['while driving', 'calmly', 'casually', 'calmly', 'inside police car']
First 5 GT:  ['drive (drive a vehicle)', 'drive (drive a vehicle)', 'drive (drive a vehicle)', 'look (vision)', 'hold (grasp, bear, keep)']
First 5 Pred:  ['talk (speak)', 'talk (speak)', 'talk (speak)', 'talk (speak)', 'talk (speak)']


{'nouns': {'rouge': {'rouge1': 0.21039944715091186,
   'rouge2': 0.07475894296009739,
   'rougeL': 0.20937437046778834,
   'rougeLsum': 0.20948472996748507},
  'meteor': {'meteor': 0.16361769091367015},
  'cider': 0.650755790528691},
 'verbs': {'rouge': {'rouge1': 0.15061013459625927,
   'rouge2': 0.11892565359477124,
   'rougeL': 0.14992967424973547,
   'rougeLsum': 0.14969128792525377},
  'meteor': {'meteor': 0.14643067863182316},
  'cider': 0.8168072063747758}}

In [1]:
import nltk
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to /home/dhruv/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

## Create Event Sentence

In [19]:
def normalize_role_name(role_name):
    """
    Normalize the 'Arg #' part of the role name by removing spaces.
    """
    return re.sub(r'Arg\s*(\d+)', r'Arg\1', role_name)

def create_event_sentence(verb, role_nouns):
    """
    Create a sentence for an event combining the verb and role-noun pairs.
    """
    role_noun_pairs = [f"{role}:{role_nouns.get(role, '')}" for role in role_nouns.keys()]
    return f"verb:{verb}, " + ", ".join(role_noun_pairs)

def evaluate_predictions(output, GT, return_dict=False):
    predictions = []
    ground_truths = []
    index = []

    for vid_seg, events in output.items():
        for event_key, event_data in events.items():
            event_gt = None
            for gt_event in GT:
                if gt_event[event_key]["vid_seg_int"] == vid_seg:
                    event_gt = gt_event[event_key]
                    break

            if not event_gt:
                print(f"No GT found for {vid_seg} {event_key}")
                continue

            gt_args = {normalize_role_name(role): gt_noun for role, gt_noun in event_gt["Args"].items()}
            predicted_verb = event_data.get("verb", "")
            ground_truth_verb = event_gt["Verb"]

            predicted_sentence = create_event_sentence(predicted_verb, event_data["nouns"])
            ground_truth_sentence = create_event_sentence(ground_truth_verb, gt_args)

            predictions.append(predicted_sentence)
            ground_truths.append(ground_truth_sentence)

            index.append(f"{vid_seg}-{event_key}")

    if return_dict:
        return {'index': index, 'predictions': predictions, 'ground_truths': ground_truths}

    results = compute_metrics(ground_truths, predictions)
    return results

def compute_metrics(decoded_labels, decoded_predictions):
    print("First 5 GT: ", decoded_labels[:5])
    print("First 5 Pred: ", decoded_predictions[:5])
    
    result = defaultdict(dict)
    for key, metric in metrics.items():
        if key in ['rouge', 'meteor']:
            # Compute the metric directly for these cases
            result[key] = metric.compute(predictions=decoded_predictions, references=decoded_labels)
        elif key in ['cider']:
            # Create dictionaries for GT and predictions as required by the CIDEr metric
            gt_dict = {cs: [decoded_labels[cs]] for cs in range(len(decoded_labels))}
            pred_dict = {cs: [decoded_predictions[cs]] for cs in range(len(decoded_predictions))}
            # Compute the CIDEr score
            cider_score = metric.compute_score(gt_dict, pred_dict)
            result[key] = cider_score[0]
    
    return dict(result)

In [20]:
evaluate_predictions(output, valid_random_GT)

First 5 GT:  ['verb:drive (drive a vehicle), Arg0 (driver):man in a black police uniform, Arg1 (vehicle or path):car, ArgM (direction):forward, ArgM (manner):casually, Scene of the Event:down a street', 'verb:drive (drive a vehicle), Arg0 (driver):man in a black police uniform, Arg1 (vehicle or path):car, ArgM (direction):forward, ArgM (manner):casually, Scene of the Event:down a street', 'verb:drive (drive a vehicle), Arg0 (driver):man in a black police uniform, Arg1 (vehicle or path):car, ArgM (direction):forward, ArgM (manner):casually, Scene of the Event:down a street', 'verb:look (vision), Arg0 (looker):man in a black police uniform, Arg1 (thing looked at or for or on):money, ArgM (direction):down, ArgM (manner):intently, Scene of the Event:car', 'verb:hold (grasp, bear, keep), Arg0 (holder):man in a black police uniform, Arg1 (thing held):money, Arg2 (benefactive):man in a black police uniform, ArgM (direction):car, ArgM (location):in a car, ArgM (manner):relieved']
First 5 Pred:

{'rouge': {'rouge1': 0.4159400892472578,
  'rouge2': 0.19335612396775914,
  'rougeL': 0.37792488528466683,
  'rougeLsum': 0.377766220148973},
 'meteor': {'meteor': 0.25571438668323765},
 'cider': 0.29953033011031555}

In [21]:
results = evaluate_predictions(output, valid_random_GT, return_dict=True)

In [24]:
import pandas as pd
df = pd.DataFrame(results)

In [25]:
df[:10]

index  \
0  v_VYQoxBs5N2A_seg_120_130-Ev1   
1  v_VYQoxBs5N2A_seg_120_130-Ev2   
2  v_VYQoxBs5N2A_seg_120_130-Ev3   
3  v_VYQoxBs5N2A_seg_120_130-Ev4   
4  v_VYQoxBs5N2A_seg_120_130-Ev5   
5   v_VYQoxBs5N2A_seg_90_100-Ev1   
6   v_VYQoxBs5N2A_seg_90_100-Ev2   
7   v_VYQoxBs5N2A_seg_90_100-Ev3   
8   v_VYQoxBs5N2A_seg_90_100-Ev4   
9   v_VYQoxBs5N2A_seg_90_100-Ev5   

                                         predictions  \
0  verb:talk (speak), Arg0 (talker):man in police...   
1  verb:talk (speak), Arg0 (talker):man in police...   
2  verb:talk (speak), Arg0 (talker):man with sung...   
3  verb:talk (speak), Arg0 (talker):police office...   
4  verb:talk (speak), Arg0 (talker):man in police...   
5  verb:fall (move downward), Arg1 (Logical subje...   
6  verb:stare (look intently), Arg0 (looker):man ...   
7  verb:grab (to capture, obtain), Arg0 (grabber)...   
8  verb:shoot (kill with gun), Arg0 (shooter):man...   
9  verb:shoot (propel projectile), Arg0 (shooter)...   

                                       ground_truths  
0  verb:drive (drive a vehicle), Arg0 (driver):ma...  
1  verb:drive (drive a vehicle), Arg0 (driver):ma...  
2  verb:drive (drive a vehicle), Arg0 (driver):ma...  
3  verb:look (vision), Arg0 (looker):man in a bla...  
4  verb:hold (grasp, bear, keep), Arg0 (holder):m...  
5  verb:collapse (fall down), Arg1 (thing collaps...  
6  verb:agonize (suffer distress), Arg1 (agonized...  
7  verb:wave (to signal (a person) or move back a...  
8  verb:approach (move towards), Arg1 (entity in ...  
9  verb:walk (walk), Arg0 (walker):man in black, ...

In [27]:
# save df
df.to_csv('./vidsituSFT_eval.csv')


In [26]:
len(df)

6120

## Remove Role Descriptions in brackets and remove ArgM


In [38]:
def normalize_role_name(role_name):
    """
    Normalize the role name by removing spaces and descriptions in brackets.
    """
    role_name = re.sub(r'Arg\s*(\d+)', r'Arg\1', role_name)  # Remove spaces in Arg numbers
    return re.sub(r'\s*\(.*?\)', '', role_name)  # Remove bracketed descriptions

def create_event_sentence(verb, role_nouns):
    """
    Create a sentence for an event combining the verb and role-noun pairs.
    """
    role_noun_pairs = [f"{normalize_role_name(role)}:{role_nouns.get(role, '')}" for role in role_nouns.keys()  if not role.startswith('ArgM')]
    return f"verb:{verb}, " + ", ".join(role_noun_pairs)

def evaluate_predictions(output, GT, return_dict=False):
    predictions = []
    ground_truths = []
    index = []

    for vid_seg, events in output.items():
        for event_key, event_data in events.items():
            event_gt = None
            for gt_event in GT:
                if gt_event[event_key]["vid_seg_int"] == vid_seg:
                    event_gt = gt_event[event_key]
                    break

            if not event_gt:
                print(f"No GT found for {vid_seg} {event_key}")
                continue

            gt_args = {normalize_role_name(role): gt_noun for role, gt_noun in event_gt["Args"].items() if not role.startswith('ArgM')}
            predicted_verb = event_data.get("verb", "")
            ground_truth_verb = event_gt["Verb"]

            predicted_sentence = create_event_sentence(predicted_verb, event_data["nouns"])
            ground_truth_sentence = create_event_sentence(ground_truth_verb, gt_args)

            predictions.append(predicted_sentence)
            ground_truths.append(ground_truth_sentence)

            index.append(f"{vid_seg}-{event_key}")

    if return_dict:
        return {'index': index, 'predictions': predictions, 'ground_truths': ground_truths}

    results = compute_metrics(ground_truths, predictions)
    return results

def compute_metrics(decoded_labels, decoded_predictions):
    print("First 5 GT: ", decoded_labels[:5])
    print("First 5 Pred: ", decoded_predictions[:5])
    
    result = defaultdict(dict)
    for key, metric in metrics.items():
        if key in ['rouge', 'meteor']:
            # Compute the metric directly for these cases
            result[key] = metric.compute(predictions=decoded_predictions, references=decoded_labels)
        elif key in ['cider']:
            # Create dictionaries for GT and predictions as required by the CIDEr metric
            gt_dict = {cs: [decoded_labels[cs]] for cs in range(len(decoded_labels))}
            pred_dict = {cs: [decoded_predictions[cs]] for cs in range(len(decoded_predictions))}
            # Compute the CIDEr score
            cider_score = metric.compute_score(gt_dict, pred_dict)
            result[key] = cider_score[0]
    
    return dict(result)

In [39]:
evaluate_predictions(output, valid_random_GT)

First 5 GT:  ['verb:drive (drive a vehicle), Arg0:man in a black police uniform, Arg1:car, Scene of the Event:down a street', 'verb:drive (drive a vehicle), Arg0:man in a black police uniform, Arg1:car, Scene of the Event:down a street', 'verb:drive (drive a vehicle), Arg0:man in a black police uniform, Arg1:car, Scene of the Event:down a street', 'verb:look (vision), Arg0:man in a black police uniform, Arg1:money, Scene of the Event:car', 'verb:hold (grasp, bear, keep), Arg0:man in a black police uniform, Arg1:money, Arg2:man in a black police uniform']
First 5 Pred:  ['verb:talk (speak), Arg0:man in police uniform, Arg2:man in passenger seat', 'verb:talk (speak), Arg0:man in police car, Arg2:person on other end of intercom', 'verb:talk (speak), Arg0:man with sunglasses, Arg2:man in police car', 'verb:talk (speak), Arg0:police officer, Arg2:person on other end of radio', 'verb:talk (speak), Arg0:man in police car, Arg2:person on other end of intercom']


{'rouge': {'rouge1': 0.4436619944959767,
  'rouge2': 0.21821858108350894,
  'rougeL': 0.41807294040009685,
  'rougeLsum': 0.4180086454769594},
 'meteor': {'meteor': 0.24603602045804976},
 'cider': 0.40444219320353914}